## IMPORT

In [ ]:
! git clone https://github.com/NVIDIA/apex.git
% cd apex
! pip install -v --no-cache-dir ./
%cd ..

Cloning into 'apex'...
remote: Enumerating objects: 26, done.
remote: Counting objects: 100% (26/26), done.
remote: Compressing objects: 100% (26/26), done.
remote: Total 7939 (delta 5), reused 12 (delta 0), pack-reused 7913
Receiving objects: 100% (7939/7939), 14.03 MiB | 21.60 MiB/s, done.
Resolving deltas: 100% (5404/5404), done.
/content/apex
Created temporary directory: /tmp/pip-ephem-wheel-cache-f21v8v85
Created temporary directory: /tmp/pip-req-tracker-mu06zap2
Created requirements tracker '/tmp/pip-req-tracker-mu06zap2'
Created temporary directory: /tmp/pip-install-hv_rbjku
Processing /content/apex
  Created temporary directory: /tmp/pip-req-build-h_cbpx0b
  Added file:///content/apex to build tracker '/tmp/pip-req-tracker-mu06zap2'
    Running setup.py (path:/tmp/pip-req-build-h_cbpx0b/setup.py) egg_info for package from file:///content/apex
    Running command python setup.py egg_info


    torch.__version__  = 1.8.1+cu101


    running egg_info
    creating /tmp/pip-req-buil

In [ ]:
from apex import amp

import pandas as pd
import numpy as np
import logging
import argparse
import random
import numpy as np
import os
import time

!pip install transformers
from transformers import BertTokenizer, BertForMultipleChoice, BertConfig, AdamW, get_linear_schedule_with_warmup
from transformers import DistilBertTokenizer, DistilBertForMultipleChoice, DistilBertConfig
import torch
from torch.optim.adam import Adam
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from torch.utils.data.distributed import DistributedSampler
from torch.nn.utils.rnn import pad_sequence

     |████████████████████████████████| 2.0MB 5.9MB/s 
     |████████████████████████████████| 870kB 18.5MB/s 
     |████████████████████████████████| 3.2MB 29.9MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.44-cp37-none-any.whl size=886084 sha256=6266d1eb87374efa997b22f20aefd95a6bb3cb6240d5039c9a725291dc02e80c
  Stored in directory: /root/.cache/pip/wheels/3e/fb/c0/13ab4d63d537658f448366744654323077c4d90069b6512f3c
Successfully built sacremoses


## Prepare MCTest Data


In [ ]:
def replace_article_str(df):
  str_lst = ['\\\\newline\\\\newline', '\\n', '\\', 'newline']
  for i in str_lst:
    df["article"] = df["article"].str.replace(i, " ", regex=True)
  return df

In [ ]:
 def mc_train():
   train_lst = []
   for i in ["160", "500"]:
     mc_train_question = pd.read_csv(
          '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTest/mc{}.train.tsv'.format(i),
          sep='\t',
          header=None,
          names=["id", "author-worktimes", "article",
                "q1", "q1_c1", "q1_c2", "q1_c3", "q1_c4",
                "q2", "q2_c1", "q2_c2", "q2_c3", "q2_c4",
                "q3", "q3_c1", "q3_c2", "q3_c3", "q3_c4",
                "q4", "q4_c1", "q4_c2", "q4_c3", "q4_c4", ])
     mc_train_ans = pd.read_csv(
        '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTest/mc{}.train.ans'.format(i),
        sep='\t',
        header=None,
        names=['q1_ans', 'q2_ans', 'q3_ans', 'q4_ans', ])   
     # Dropping id and author-worktimes columns
     mc_train = mc_train_question.drop(columns=["id", "author-worktimes"])
     mc_train = mc_dataset_pre(mc_train, mc_train_ans)
     mc_train = replace_article_str(mc_train)
     train_lst.append(mc_train)
   final_train_df = pd.concat(train_lst, ignore_index=True)
   return final_train_df

def mc_dev():
   dev_lst = []
   for i in ["160", "500"]: 
      mc_dev_question = pd.read_csv(
          '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTest/mc{}.dev.tsv'.format(i),
          sep='\t',
          header=None,
          names=["id", "author-worktimes", "article",
                 "q1", "q1_c1", "q1_c2", "q1_c3", "q1_c4",
                 "q2", "q2_c1", "q2_c2", "q2_c3", "q2_c4",
                 "q3", "q3_c1", "q3_c2", "q3_c3", "q3_c4",
                 "q4", "q4_c1", "q4_c2", "q4_c3", "q4_c4", ])
      mc_dev_ans = pd.read_csv(
          '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTest/mc{}.dev.ans'.format(i),
          sep='\t',
          header=None,
          names=['q1_ans', 'q2_ans', 'q3_ans', 'q4_ans', ])     
      # Dropping id and author-worktimes columns
      mc_dev = mc_dev_question.drop(columns=["id", "author-worktimes"])
      mc_dev = mc_dataset_pre(mc_dev, mc_dev_ans)
      mc_dev = replace_article_str(mc_dev)
      # mc_dev['article'] = mc_dev['article'].str.replace("\\"," ")
      # mc_dev['article'] = mc_dev['article'].str.replace("\ newline"," ")
      dev_lst.append(mc_dev)
   final_dev_df = pd.concat(dev_lst, ignore_index=True)
   return final_dev_df
 

 def mc_test():
   test_lst = []
   for i in ["160", "500"]:
      mc_test_question = pd.read_csv(
          '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTest/mc{}.test.tsv'.format(i),
          sep='\t',
          header=None,
          names=["id", "author-worktimes", "article",
                 "q1", "q1_c1", "q1_c2", "q1_c3", "q1_c4",
                 "q2", "q2_c1", "q2_c2", "q2_c3", "q2_c4",
                 "q3", "q3_c1", "q3_c2", "q3_c3", "q3_c4",
                 "q4", "q4_c1", "q4_c2", "q4_c3", "q4_c4", ])
      mc_test_ans = pd.read_csv(
          '/content/gdrive/MyDrive/Colab Notebooks/COMP5423_Project/datasets/MCTest/MCTestAnswers/mc{}.test.ans'.format(i),
          sep='\t',
          header=None,
          names=['q1_ans', 'q2_ans', 'q3_ans', 'q4_ans', ])     
      # Dropping id and author-worktimes columns
      mc_test = mc_test_question.drop(columns=["id", "author-worktimes"])
      mc_test = mc_dataset_pre(mc_test, mc_test_ans)
      mc_test = replace_article_str(mc_test)
      # mc_test['article'] = mc_test['article'].str.replace("\n"," ")
      # mc_test['article'] = mc_test['article'].str.replace("\ newline"," ")
      test_lst.append(mc_test)
   final_test_df = pd.concat(test_lst, ignore_index=True)
   return final_test_df

In [ ]:
# mc_train().loc[1300:1400, "article"].values

In [ ]:
def mc_dataset_pre(df, df_ans):
    # Adding new column of the required sentence type of the answer
    for i in range(1, 5):
        df.insert(loc=df.columns.get_loc("q{}".format(str(i))) + 1,
                  column="q{}_ans_sen_type".format(i),
                  value="")
    # Checking what sentence type is required for finding the answer
    for i in range(1, 5):
        for k in range(df.shape[0]):
            if "multiple:" in df.loc[k, "q{}".format(str(i))].split()[0]:
                df.loc[k, "q{}_ans_sen_type".format(i)] = "multiple"
                df.loc[k, "q{}".format(str(i))] = df.loc[k, "q{}".format(str(i))].replace("multiple:", "")
            elif "one:" in df.loc[k, "q{}".format(str(i))].split()[0]:
                df.loc[k, "q{}_ans_sen_type".format(i)] = "one"
                df.loc[k, "q{}".format(str(i))] = df.loc[k, "q{}".format(str(i))].replace("one:", "")

    # Adding a new column of the question answer
    for i in range(1, 5):
        df.insert(loc=df.columns.get_loc("q{}_c4".format(str(i))) + 1,
                    column="q{}_ans".format(i),
                    value=df_ans.iloc[:, i - 1])

    # Adding a new column of the text of the question answer
    for i in range(1, 5):
        df.insert(loc=df.columns.get_loc("q{}_ans".format(str(i))) + 1,
                  column="q{}_ans_text".format(i),
                  value="")

    # Putting the corresponding answer of the question into the dataframe
    for i in range(1, 5):
        for k in range(df.shape[0]):
            if df.loc[k, "q{}_ans".format(str(i))] == "A":
                df.loc[k, "q{}_ans_text".format(str(i))] = df.loc[k, "q{}_c1".format(str(i))]
            elif df.loc[k, "q{}_ans".format(str(i))] == "B":
                df.loc[k, "q{}_ans_text".format(str(i))] = df.loc[k, "q{}_c2".format(str(i))]
            elif df.loc[k, "q{}_ans".format(str(i))] == "C":
                df.loc[k, "q{}_ans_text".format(str(i))] = df.loc[k, "q{}_c3".format(str(i))]
            elif df.loc[k, "q{}_ans".format(str(i))] == "D":
                df.loc[k, "q{}_ans_text".format(str(i))] = df.loc[k, "q{}_c4".format(str(i))]

    # Get the column of article, question, answer sentence type and answer from training dataset
    # Put them into a final training dataset
    df_final = pd.DataFrame(columns=["article", "question", "option_1", "option_2", "option_3", "option_4",
                                     "ans_sen_type", "answer"])
    for art in range(df.shape[0]):
        for q in range(1, 5):
            df_final = df_final.append(pd.DataFrame([[df.loc[art, "article"],
                                                      df.loc[art, "q{}".format(str(q))],
                                                      df.loc[art, "q{}_c1".format(str(q))],
                                                      df.loc[art, "q{}_c2".format(str(q))],
                                                      df.loc[art, "q{}_c3".format(str(q))],
                                                      df.loc[art, "q{}_c4".format(str(q))],
                                                      df.loc[art, "q{}_ans_sen_type".format(str(q))],
                                                      df.loc[art, "q{}_ans".format(str(q))]
                                                      # df.loc[art, "q{}_ans_text".format(str(q))]
                                                      ]],
                                                    columns=["article", "question", "option_1", "option_2", "option_3",
                                                             "option_4",
                                                             "ans_sen_type", "answer"]),
                                       ignore_index=True)
    return df_final

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).


### MC Train

In [ ]:
mc_train()

article  ... answer
0     Tom had to fix some things around the house. H...  ...      C
1     Tom had to fix some things around the house. H...  ...      D
2     Tom had to fix some things around the house. H...  ...      B
3     Tom had to fix some things around the house. H...  ...      C
4     Lisa has a pet cat named Whiskers. Whiskers is...  ...      D
...                                                 ...  ...    ...
1475  Once there was a boy named Bill who liked to p...  ...      D
1476  This summer Frank and his friends went to Boy ...  ...      A
1477  This summer Frank and his friends went to Boy ...  ...      D
1478  This summer Frank and his friends went to Boy ...  ...      C
1479  This summer Frank and his friends went to Boy ...  ...      D

[1480 rows x 8 columns]

### MC Dev

In [ ]:
mc_dev()

article  ... answer
0    It was Jessie Bear's birthday. She was having ...  ...      A
1    It was Jessie Bear's birthday. She was having ...  ...      C
2    It was Jessie Bear's birthday. She was having ...  ...      B
3    It was Jessie Bear's birthday. She was having ...  ...      B
4    Sally had a very exciting summer vacation. She...  ...      C
..                                                 ...  ...    ...
315  Jack and Mackenzie wanted to do something fun ...  ...      B
316  Lucy is an eight year old girl who lives with ...  ...      A
317  Lucy is an eight year old girl who lives with ...  ...      A
318  Lucy is an eight year old girl who lives with ...  ...      B
319  Lucy is an eight year old girl who lives with ...  ...      A

[320 rows x 8 columns]

### MC Test

In [ ]:
mc_test()

article  ... answer
0    Todd is a small boy in the town of Rocksville....  ...      A
1    Todd is a small boy in the town of Rocksville....  ...      A
2    Todd is a small boy in the town of Rocksville....  ...      B
3    Todd is a small boy in the town of Rocksville....  ...      B
4    Mortamer was a tree monkey who lived in the ju...  ...      D
..                                                 ...  ...    ...
835  Greg and his mother were building a racing car...  ...      B
836  Joey went to a baseball game during the winter...  ...      A
837  Joey went to a baseball game during the winter...  ...      D
838  Joey went to a baseball game during the winter...  ...      D
839  Joey went to a baseball game during the winter...  ...      D

[840 rows x 8 columns]

## Tokenization & Model

In [ ]:
def tokenization(): 
    tokenizer = BertTokenizer.from_pretrained('bert-large-uncased')
    return tokenizer

In [ ]:
def mc_model():
    config = BertConfig.from_pretrained('bert-large-uncased', num_labels=4)
    model = BertForMultipleChoice.from_pretrained('bert-large-uncased', config=config)
    return model

In [ ]:
def _truncate_seq_pair(tokens_a, tokens_b, max_length):
    """Truncates a sequence pair in place to the maximum length."""

    while True:
        total_length = len(tokens_a) + len(tokens_b)
        if total_length <= max_length:
            break
        if len(tokens_a) > len(tokens_b):
            tokens_a.pop()
        else:
            tokens_b.pop()

## MCTest Features Class

In [ ]:
class InputMCTestFeatures(object):
    def __init__(self,
                 example_id,
                 choices_features,
                 label):
        self.example_id = example_id
        self.choices_features = [
            {
                'input_ids': input_ids,
                'segment_ids': segment_ids,
                'input_mask': input_mask
            }
            for _, input_ids, segment_ids, input_mask in choices_features
        ]
        self.label = label

## MCTest Object Class

In [ ]:
class mc160(object):
    def __init__(self,
                 test_id,
                 article,
                 start_ending,
                 ending_1,
                 ending_2,
                 ending_3,
                 ending_4,
                 label):
        self.test_id = test_id
        self.article = article
        self.start_ending = start_ending
        self.endings = [
            ending_1,
            ending_2,
            ending_3,
            ending_4,
        ]
        self.label = label

    def __str__(self):
        return self.__repr__()

    def __repr__(self):
        l = [
            "id: {}".format(self.test_id),
            "article: {}".format(self.article),
            "question: {}".format(self.start_ending),
            "option_1: {}".format(self.endings[0]),
            "option_2: {}".format(self.endings[1]),
            "option_3: {}".format(self.endings[2]),
            "option_4: {}".format(self.endings[3]),
        ]


        if self.label is not None:
            l.append("label: {}".format(self.label))

        return ", ".join(l)

## MCTest Dataset

In [ ]:
def mctestDataSet(tokenizer, task_type, max_seq_length):
    df = None
    if task_type == "train":
        df = mc_train()
    elif task_type == "dev":
        df = mc_dev()
    elif task_type == "test":
        df = mc_test()
  
    examples = []
    for i in range(df.shape[0]):
        answer = ord(df.loc[i, "answer"]) - ord('A')
        examples.append(mc160(
            test_id="{}_{}-{}".format("mc", task_type, i),
            article=df.loc[i, "article"],
            start_ending=df.loc[i, "question"],
            ending_1=df.loc[i, "option_1"],
            ending_2=df.loc[i, "option_2"],
            ending_3=df.loc[i, "option_3"],
            ending_4=df.loc[i, "option_4"],
            label=answer
        ))

    features = []
    for example_index, example in enumerate(examples):
        # article tokens
        article_tokens = tokenizer.tokenize(example.article)
        # quesiton tokens
        start_ending_tokens = tokenizer.tokenize(example.start_ending)

        choices_features = []
        for ending_index, ending in enumerate(example.endings):
            article_tokens_choice = article_tokens[:]
            ending_tokens = start_ending_tokens + ["[SEP]"] + tokenizer.tokenize(ending)
            encode = tokenizer.encode_plus(article_tokens_choice, 
                                           ending_tokens,
                                           add_special_tokens=True,
                                           padding='max_length',
                                           truncation=True,
                                           max_length=max_seq_length)
            
            input_ids = encode["input_ids"]
            segments_ids = encode["token_type_ids"]
            input_mask = encode["attention_mask"]
            tokens = tokenizer.decode(input_ids)
            print("input_ids" ,input_ids)
            print("segments_ids" ,segments_ids)
            print("input_mask" ,input_mask)
            print("token" ,tokens)
            
            assert len(input_ids) == max_seq_length
            assert len(input_mask) == max_seq_length
            assert len(segments_ids) == max_seq_length

            choices_features.append((tokens, input_ids, segments_ids, input_mask))

        label = example.label
        features.append(InputMCTestFeatures(
            example_id=example.test_id,
            choices_features=choices_features,
            label=label
        ))


    tensor_input_ids = torch.tensor([[choice["input_ids"] for choice in feature.choices_features] for feature in features], dtype=torch.long)
    tensor_segment_ids = torch.tensor([[choice["segment_ids"] for choice in feature.choices_features] for feature in features], dtype=torch.long)
    tensor_input_mask = torch.tensor([[choice["input_mask"] for choice in feature.choices_features] for feature in features], dtype=torch.long)
    tensor_labels = torch.tensor([f.label for f in features], dtype=torch.long)   
    tensor_dataset = TensorDataset(tensor_input_ids, tensor_segment_ids, tensor_input_mask, tensor_labels)  
      
    if task_type == "test":
      new_test_data = []
      for i in tensor_dataset:
        new_input_ids = i[0]
        new_segment_ids = i[1]
        new_input_masks = i[2]
        # new_labels = None
        # new_test_data.append([new_input_ids, new_segment_ids, new_input_masks, new_labels])
        new_test_data.append([new_input_ids, new_segment_ids, new_input_masks])
      tensor_dataset = tuple(new_test_data)

    return tensor_dataset

## Defining GPU

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

In [ ]:
!nvidia-smi

Mon Apr  5 12:02:57 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.67       Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P0    27W / 250W |      2MiB / 16280MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

## Prediction

In [ ]:
def get_predictions(model, dataloader, compute_acc=False):
    predictions = None
    correct = 0
    total = 0
  
    with torch.no_grad():
        for data in dataloader:
            if next(model.parameters()).is_cuda:
                data = [t.to(device) for t in data if t is not None]
            
            tokens_tensors, segments_tensors, masks_tensors = data[:3]
            outputs = model(input_ids=tokens_tensors, 
                            token_type_ids=segments_tensors, 
                            attention_mask=masks_tensors)
            
            logits = outputs[0]
            # print("logits: {}".format(logits))
                        
            _, pred = torch.max(logits.data, 1)
            
            if compute_acc:
                labels = data[3]
                total += labels.size(0)
                correct += (pred == labels).sum().item()
                
            if predictions is None:
                predictions = pred
            else:
                predictions = torch.cat((predictions, pred))
    
    if compute_acc:
        acc = correct / total
        return predictions, acc
    return predictions

## Run MCTest

In [ ]:
def run_mctest():
    torch.cuda.empty_cache()
    tokenizer = tokenization()

    model = mc_model()
    model = model.to(device)
  
    train_data = mctestDataSet(tokenizer, "train", 128)

    train_sampler = RandomSampler(train_data)
    train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=6)
    #train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=4)
      
    # adam_optimizer = Adam(model.parameters(), lr=1e-5)
    no_decay = ['bias', 'LayerNorm.weight']
    optimizer_grouped_parameters = [
        {'params': [p for n, p in model.named_parameters() if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},
        {'params': [p for n, p in model.named_parameters() if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
    ]
    adam_optimizer = AdamW(optimizer_grouped_parameters, lr=1e-5)
    model, adam_optimizer = amp.initialize(model, adam_optimizer, opt_level="O1")

    EPOCHS = 8
    for epoch in range(EPOCHS):
        epoch_start = time.time()
        running_loss = 0.0
        t0_epoch, t0_batch = time.time(), time.time()
        total_loss, batch_loss, batch_counts = 0, 0, 0
        model.train()

        # for data in train_dataloader:
        for data in train_dataloader:
          tokens_tensors, segments_tensors, masks_tensors, labels_tensor = [t.to(device) for t in data]
          
          # Set the gradient to 0
          adam_optimizer.zero_grad()

          outputs = model(input_ids=tokens_tensors, 
                          token_type_ids=segments_tensors, 
                          attention_mask=masks_tensors, 
                          labels=labels_tensor)
          
          # print("outputs: {}".format(outputs))
          
          loss = outputs[0]
          
          running_loss += loss.item()

          with amp.scale_loss(loss, adam_optimizer) as scaled_loss:
            scaled_loss.backward()

          adam_optimizer.step()

        # Calculating Accuracy
        _, acc = get_predictions(model, train_dataloader, compute_acc=True)
        epoch_end = time.time()
        # print('[epoch %d] loss: %.3f, acc: %.3f' % (epoch + 1, running_loss, acc))
        print("Training Epoch: {}, Loss: {}, Accuracy: {}, Epcoh Time: {}".format(epoch+1, running_loss, acc, epoch_end-epoch_start))
    return model
    
model = run_mctest()

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertForMultipleChoice: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForMultipleChoice from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMultipleChoice from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForMultipleChoice were not initialized from the model checkpoint at bert-large-uncased and are new

Streaming output truncated to the last 5000 lines.
token [CLS] the kitty did not want to freeze, so it found a place to stay warm in a trashcan near a bush. the kitty had been left outside in the rain, but some friendly people thought that they would let it in when they found it in the trashcan outside. they gave the kitty some water to sip, and food to eat. when the phone would ring, the kitty would run and hide. the kitty would hide in the bathroom. sometimes, the kitty would take its food into the bedroom and eat it there. the kitty's claws were so [SEP] where did the kitty hide first? [SEP] in a bush. [SEP]
input_ids [101, 1996, 14433, 2106, 2025, 2215, 2000, 13184, 1010, 2061, 2009, 2179, 1037, 2173, 2000, 2994, 4010, 1999, 1037, 11669, 9336, 2379, 1037, 5747, 1012, 1996, 14433, 2018, 2042, 2187, 2648, 1999, 1996, 4542, 1010, 2021, 2070, 5379, 2111, 2245, 2008, 2027, 2052, 2292, 2009, 1999, 2043, 2027, 2179, 2009, 1999, 1996, 11669, 9336, 2648, 1012, 2027, 2435, 1996, 14433, 2070,

## Evaluation

In [ ]:
# ## Evaluation
# model.eval()    
# tokenizer = tokenization()
# dev_data = mctestDataSet(tokenizer=tokenizer, task_type="dev", max_seq_length=128)
# dev_dataloader = DataLoader(dev_data, batch_size=8)   
# # Tracking variables
# dev_accuracy = []
# dev_loss = []   
# eval_time_start = time.time()
# # For each batch in our validation set...
# for data in dev_dataloader:
#     # Load batch to GPU
#     tokens_tensors, segments_tensors, masks_tensors, labels_tensor = [t.to(device) for t in data]   
#     # Compute logits
#     with torch.no_grad():
#       outputs = model(input_ids=tokens_tensors, 
#                   token_type_ids=segments_tensors, 
#                   attention_mask=masks_tensors, 
#                   labels=labels_tensor)
#     loss = outputs[0]
#     logits = outputs[1]
#     # Compute loss
#     dev_loss.append(loss.item())    
#     # Get the predictions
#     preds = torch.argmax(logits, dim=1).flatten()   
#     # Calculating Accuracy
# _, accuracy = get_predictions(model, dev_dataloader, compute_acc=True)
# dev_accuracy.append(accuracy)
# eval_time_stop = time.time()    
# # Compute the average accuracy and loss over the validation set.
# dev_loss = np.mean(dev_loss)
# dev_accuracy = np.mean(dev_accuracy)
# print("Average Evaluation Result - Loss: {}, Accuracy: {}, Time: {}".format(dev_loss,
#                                                                             dev_accuracy,
#                                                                             eval_time_stop-eval_time_start))

## Saving Model

In [ ]:
torch.save(model.state_dict(), 'checkpoint.pth')

## Loading Model

In [ ]:
state_dict = torch.load('checkpoint.pth')
print(state_dict.keys())

odict_keys(['bert.embeddings.position_ids', 'bert.embeddings.word_embeddings.weight', 'bert.embeddings.position_embeddings.weight', 'bert.embeddings.token_type_embeddings.weight', 'bert.embeddings.LayerNorm.weight', 'bert.embeddings.LayerNorm.bias', 'bert.encoder.layer.0.attention.self.query.weight', 'bert.encoder.layer.0.attention.self.query.bias', 'bert.encoder.layer.0.attention.self.key.weight', 'bert.encoder.layer.0.attention.self.key.bias', 'bert.encoder.layer.0.attention.self.value.weight', 'bert.encoder.layer.0.attention.self.value.bias', 'bert.encoder.layer.0.attention.output.dense.weight', 'bert.encoder.layer.0.attention.output.dense.bias', 'bert.encoder.layer.0.attention.output.LayerNorm.weight', 'bert.encoder.layer.0.attention.output.LayerNorm.bias', 'bert.encoder.layer.0.intermediate.dense.weight', 'bert.encoder.layer.0.intermediate.dense.bias', 'bert.encoder.layer.0.output.dense.weight', 'bert.encoder.layer.0.output.dense.bias', 'bert.encoder.layer.0.output.LayerNorm.weigh

In [ ]:
model = mc_model()
model = model.to(device)
model.load_state_dict(state_dict)

Some weights of the model checkpoint at bert-large-uncased were not used when initializing BertForMultipleChoice: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias']
- This IS expected if you are initializing BertForMultipleChoice from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMultipleChoice from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForMultipleChoice were not initialized from the model checkpoint at bert-large-uncased and are new

<All keys matched successfully>

## Test Prediction

In [ ]:
model.eval()
tokenizer = tokenization()

test_data = mctestDataSet(tokenizer=tokenizer, task_type="test", max_seq_length=128)

test_dataloader = DataLoader(test_data, batch_size=8)

predictions = get_predictions(model, test_dataloader)

# Testing Result Evaluation
from sklearn.metrics import accuracy_score

label_map = {'A': 0, 'B': 1, 'C': 2, 'D': 3}
index_map = {v: k for k, v in label_map.items()}

df = pd.DataFrame({"pre_answer": predictions.tolist()})
df['pre_answer'] = df.pre_answer.apply(lambda x: index_map[x])
df_pred = pd.concat([mc_test().loc[:, ["article"]], 
                     mc_test().loc[:, ["question"]], 
                     mc_test().loc[:, ["answer"]], 
                     df.loc[:, 'pre_answer']], axis=1)

list_true = df_pred.loc[:, ["answer"]].values.tolist()
list_pre = df_pred.loc[:, ["pre_answer"]].values.tolist()

print("Testing Accuracy: {}".format(accuracy_score(list_true, list_pre)))

Streaming output truncated to the last 5000 lines.
segments_ids [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
input_mask [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
token [CLS] the dog walked around the city. he was looking around. he was trying to find food. he smelled the trashcan to see what might be inside. he did 

In [ ]:
df_pred

article  ... pre_answer
0    Todd is a small boy in the town of Rocksville....  ...          D
1    Todd is a small boy in the town of Rocksville....  ...          D
2    Todd is a small boy in the town of Rocksville....  ...          B
3    Todd is a small boy in the town of Rocksville....  ...          A
4    Mortamer was a tree monkey who lived in the ju...  ...          D
..                                                 ...  ...        ...
835  Greg and his mother were building a racing car...  ...          B
836  Joey went to a baseball game during the winter...  ...          A
837  Joey went to a baseball game during the winter...  ...          C
838  Joey went to a baseball game during the winter...  ...          D
839  Joey went to a baseball game during the winter...  ...          A

[840 rows x 4 columns]